## **DAA - Dados e Aprendizagem Automática**
### MCI to AD Progression Prediction Using Brain MRI Analysis
#### Group 2

In [172]:
import sklearn as skl
import pandas as pd
pd.set_option('display.max_info_columns', 3000)
pd.set_option('display.max_columns', 3000)
pd.set_option('display.max_rows', 3000)
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, StratifiedShuffleSplit
from sklearn import tree

from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier, VotingClassifier, BaggingClassifier, StackingClassifier
from sklearn.linear_model import LogisticRegression
import xgboost as xgb
from xgboost.sklearn import XGBClassifier

from sklearn.metrics import classification_report
%matplotlib inline

from Projeto.repo.DAA.main import preprocess

### **Data Analysis / Preparation**

**Import dataset**

In [193]:
df = pd.read_csv('datasets/test_radiomics_hipocamp.csv')

In [174]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 305 entries, 0 to 304
Data columns (total 2181 columns):
 #     Column                                                         Non-Null Count  Dtype  
---    ------                                                         --------------  -----  
 0     ID                                                             305 non-null    object 
 1     Image                                                          305 non-null    object 
 2     Mask                                                           305 non-null    object 
 3     diagnostics_Versions_PyRadiomics                               305 non-null    object 
 4     diagnostics_Versions_Numpy                                     305 non-null    object 
 5     diagnostics_Versions_SimpleITK                                 305 non-null    object 
 6     diagnostics_Versions_PyWavelet                                 305 non-null    object 
 7     diagnostics_Versions_Python             

In [175]:
df.head()

ID                                              Image  \
0  006_S_0681  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  941_S_1203  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  011_S_0003  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  057_S_0779  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  033_S_0920  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

                                                Mask  \
0  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

  diagnostics_Versions_PyRadiomics diagnostics_Versions_Numpy  \
0                            2.2.0                     1.18.5   
1                            2.2.0                     1.18.5   
2                            2.2.0                     1.18.5   
3                            2.2.0                     1.18.5   
4                            2.2.0                     1.18.5   

  diagnostics_Versions_SimpleITK diagnostics_Versions_PyWavelet  \
0                          1.2.4                          1.1.1   
1                          1.2.4                          1.1.1   
2                          1.2.4                          1.1.1   
3                          1.2.4                          1.1.1   
4                          1.2.4                          1.1.1   

  diagnostics_Versions_Python  \
0                       3.7.7   
1                       3.7.7   
2                       3.7.7   
3                       3.7.7   
4                       3.7.7   

                  diagnostics_Configuration_Settings  \
0  {'minimumROIDimensions': 2, 'minimumROISize': ...   
1  {'minimumROIDimensions': 2, 'minimumROISize': ...   
2  {'minimumROIDimensions': 2, 'minimumROISize': ...   
3  {'minimumROIDimensions': 2, 'minimumROISize': ...   
4  {'minimumROIDimensions': 2, 'minimumROISize': ...   

         diagnostics_Configuration_EnabledImageTypes  \
0  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
1  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
2  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
3  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
4  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   

            diagnostics_Image-original_Hash  \
0  b5d774a32163a7ee822d42a07808a787f8687f56   
1  397042d736bd790b7880b372b1749ff424f89cbe   
2  84d679a88812c4aaf03a6d99f00c913b2f64506f   
3  168f330d2ca3f097146e5d041f33b40672d230df   
4  ea5f291ea107dfda5e5c725eae7c0555ced44ce4   

   diagnostics_Image-original_Dimensionality  \
0                                          3   
1                                          3   
2                                          3   
3                                          3   
4                                          3   

  diagnostics_Image-original_Spacing diagnostics_Image-original_Size  \
0                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
1                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
2                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
3                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
4                    (1.0, 1.0, 1.0)                 (256, 256, 256)   

   diagnostics_Image-original_Mean  diagnostics_Image-original_Minimum  \
0                         5.848123                                   0   
1                         5.238834                                   0   
2                         6.816667                                   0   
3                         6.445162                                   0   
4                         5.568269                                   0   

   diagnostics_Image-original_Maximum  \
0                                 178   
1                                 190   
2                        

**Missing values?**

In [176]:
print("Total:", df.isna().sum().sum())

Total: 0


**Repeated values?**

In [194]:
# drop duplicate rows
prev = len(df)
df.drop_duplicates(inplace=True)
print("Total rows:", len(df))

Total rows: 100


**Columns with always-repeated values?**

In [195]:
unique_dict = df.nunique().to_dict()
no_unique_values = {col: count for col, count in unique_dict.items() if count == 1}
print("Total:",df.nunique().tolist().count(1))

Total: 159


**Drop columns with always-repeated values**

In [196]:
drop = [col for col, _ in no_unique_values.items()]
df.drop(drop, axis=1, inplace=True)
df.head()

ID                                              Image  \
0  941_S_1194  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_119...   
1  036_S_0945  /notebooks/disk2/DS2_FreeSurfer/ADNI_036_S_094...   
2  024_S_1171  /notebooks/disk2/DS2_FreeSurfer/ADNI_024_S_117...   
3  035_S_0555  /notebooks/disk2/DS2_FreeSurfer/ADNI_035_S_055...   
4  023_S_0081  /notebooks/disk2/DS2_FreeSurfer/ADNI_023_S_008...   

                                                Mask  \
0  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_119...   
1  /notebooks/disk2/DS2_FreeSurfer/ADNI_036_S_094...   
2  /notebooks/disk2/DS2_FreeSurfer/ADNI_024_S_117...   
3  /notebooks/disk2/DS2_FreeSurfer/ADNI_035_S_055...   
4  /notebooks/disk2/DS2_FreeSurfer/ADNI_023_S_008...   

            diagnostics_Image-original_Hash  diagnostics_Image-original_Mean  \
0  b4977b66eca7c1e38c03fb5193cca7ca01dd46ec                         5.936274   
1  43850cb7e611c0438dbf2fee1f5800d548de621f                         6.727111   
2  a27b647efa22a9d77a17a07e92657722a268552d                         6.788788   
3  cbd443cf571aaa826bebc6cc9d4bf80f91afd938                         6.925492   
4  41ce7f75ad8398dc3a8dfe4ea5debd4a84aac204                         5.273378   

   diagnostics_Image-original_Maximum  \
0                                 138   
1                                 179   
2                                 161   
3                                 165   
4                                 176   

             diagnostics_Mask-original_Hash  \
0  b9cd2759de5fb379af13626ecc9b71f841df44c0   
1  fbd8a283b4ad67264a096d5493c0e7663449f22a   
2  3610f06f74981f83e23fa930825a6ba36faabcee   
3  46f300320ae71541ff921d9e861af041bead5051   
4  400a079bcf1ce0a02456918b5f8e2b17a148c7eb   

  diagnostics_Mask-original_BoundingBox  diagnostics_Mask-original_VoxelNum  \
0             (92, 123, 90, 42, 29, 76)                                6746   
1             (79, 135, 90, 48, 16, 78)                                8182   
2            (105, 112, 87, 45, 27, 80)                                7765   
3             (88, 110, 88, 42, 30, 84)                                8493   
4             (88, 145, 94, 45, 21, 71)                                7257   

         diagnostics_Mask-original_CenterOfMassIndex  \
0  (114.35013341239252, 137.93240438778537, 127.3...   
1  (105.5636763627475, 144.51344414568564, 127.57...   
2  (128.06696716033483, 125.64842240824211, 125.5...   
3  (110.5198398681267, 125.62310137760508, 130.65...   
4  (112.50337605070966, 155.2838638555877, 129.34...   

              diagnostics_Mask-original_CenterOfMass  \
0  (114.35013341239252, 137.93240438778537, 127.3...   
1  (105.5636763627475, 144.51344414568564, 127.57...   
2  (128.06696716033483, 125.64842240824211, 125.5...   
3  (110.5198398681267, 125.62310137760508, 130.65...   
4  (112.50337605070966, 155.2838638555877, 129.34...   

   original_shape_Elongation  original_shape_Flatness  \
0                   0.407223                 0.096929   
1                   0.432795                 0.096712   
2                   0.422635                 0.107836   
3                   0.411789                 0.104226   
4                   0.437484                 0.099548   

   original_shape_LeastAxisLength  original_shape_MajorAxisLength  \
0                       10.641164                      109.782918   
1                       10.249435                      105.979255   
2                       11.116675                      103.088450   
3                       11.324564                      108.653645   
4                       10.281734                      103.283883   

   original_shape_Maximum2DDiameterColumn  \
0                               76.400262   
1                               77.103826   
2                               76.006579   
3                               81.024688   
4                               73.389373   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlic

**Categorical features**

In [197]:
for col in [col for col in df.columns if df[col].dtype == 'object']:
    print(col)

ID
Image
Mask
diagnostics_Image-original_Hash
diagnostics_Mask-original_Hash
diagnostics_Mask-original_BoundingBox
diagnostics_Mask-original_CenterOfMassIndex
diagnostics_Mask-original_CenterOfMass


**Categorical features with all-unique values?**

In [198]:
all_unique = [col for col, count in unique_dict.items() if count == df.shape[0] and df[col].dtype == 'object']
for col in all_unique:
    print(col)

ID
Image
Mask
diagnostics_Image-original_Hash
diagnostics_Mask-original_Hash
diagnostics_Mask-original_BoundingBox
diagnostics_Mask-original_CenterOfMassIndex
diagnostics_Mask-original_CenterOfMass


In [199]:
df.filter(items=all_unique).head()

ID                                              Image  \
0  941_S_1194  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_119...   
1  036_S_0945  /notebooks/disk2/DS2_FreeSurfer/ADNI_036_S_094...   
2  024_S_1171  /notebooks/disk2/DS2_FreeSurfer/ADNI_024_S_117...   
3  035_S_0555  /notebooks/disk2/DS2_FreeSurfer/ADNI_035_S_055...   
4  023_S_0081  /notebooks/disk2/DS2_FreeSurfer/ADNI_023_S_008...   

                                                Mask  \
0  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_119...   
1  /notebooks/disk2/DS2_FreeSurfer/ADNI_036_S_094...   
2  /notebooks/disk2/DS2_FreeSurfer/ADNI_024_S_117...   
3  /notebooks/disk2/DS2_FreeSurfer/ADNI_035_S_055...   
4  /notebooks/disk2/DS2_FreeSurfer/ADNI_023_S_008...   

            diagnostics_Image-original_Hash  \
0  b4977b66eca7c1e38c03fb5193cca7ca01dd46ec   
1  43850cb7e611c0438dbf2fee1f5800d548de621f   
2  a27b647efa22a9d77a17a07e92657722a268552d   
3  cbd443cf571aaa826bebc6cc9d4bf80f91afd938   
4  41ce7f75ad8398dc3a8dfe4ea5debd4a84aac204   

             diagnostics_Mask-original_Hash  \
0  b9cd2759de5fb379af13626ecc9b71f841df44c0   
1  fbd8a283b4ad67264a096d5493c0e7663449f22a   
2  3610f06f74981f83e23fa930825a6ba36faabcee   
3  46f300320ae71541ff921d9e861af041bead5051   
4  400a079bcf1ce0a02456918b5f8e2b17a148c7eb   

  diagnostics_Mask-original_BoundingBox  \
0             (92, 123, 90, 42, 29, 76)   
1             (79, 135, 90, 48, 16, 78)   
2            (105, 112, 87, 45, 27, 80)   
3             (88, 110, 88, 42, 30, 84)   
4             (88, 145, 94, 45, 21, 71)   

         diagnostics_Mask-original_CenterOfMassIndex  \
0  (114.35013341239252, 137.93240438778537, 127.3...   
1  (105.5636763627475, 144.51344414568564, 127.57...   
2  (128.06696716033483, 125.64842240824211, 125.5...   
3  (110.5198398681267, 125.62310137760508, 130.65...   
4  (112.50337605070966, 155.2838638555877, 129.34...   

              diagnostics_Mask-original_CenterOfMass  
0  (114.35013341239252, 137.93240438778537, 127.3...  
1  (105.5636763627475, 144.51344414568564, 127.57...  
2  (128.06696716033483, 125.64842240824211, 125.5...  
3  (110.5198398681267, 125.62310137760508, 130.65...  
4  (112.50337605070966, 155.2838638555877, 129.34...

The features `diagnostics_Mask-original_BoundingBox`, `diagnostics_Mask-original_CenterOfMassIndex` and `diagnostics_Mask-original_CenterOfMass` contain valuable information about the size, location and center of mass of the hippocampus, in the form of coordinates, and therefore could be useful for our model.

The remaining features have all-unique string values representing image paths and hashes, and therefore aren't useful for our model.

**Drop unuseful all-unique categorical columns**

In [200]:
df.drop(list(set(all_unique) - set(['diagnostics_Mask-original_BoundingBox', 'diagnostics_Mask-original_CenterOfMassIndex', 'diagnostics_Mask-original_CenterOfMass'])), axis=1, inplace=True)
df.head()

diagnostics_Image-original_Mean  diagnostics_Image-original_Maximum  \
0                         5.936274                                 138   
1                         6.727111                                 179   
2                         6.788788                                 161   
3                         6.925492                                 165   
4                         5.273378                                 176   

  diagnostics_Mask-original_BoundingBox  diagnostics_Mask-original_VoxelNum  \
0             (92, 123, 90, 42, 29, 76)                                6746   
1             (79, 135, 90, 48, 16, 78)                                8182   
2            (105, 112, 87, 45, 27, 80)                                7765   
3             (88, 110, 88, 42, 30, 84)                                8493   
4             (88, 145, 94, 45, 21, 71)                                7257   

         diagnostics_Mask-original_CenterOfMassIndex  \
0  (114.35013341239252, 137.93240438778537, 127.3...   
1  (105.5636763627475, 144.51344414568564, 127.57...   
2  (128.06696716033483, 125.64842240824211, 125.5...   
3  (110.5198398681267, 125.62310137760508, 130.65...   
4  (112.50337605070966, 155.2838638555877, 129.34...   

              diagnostics_Mask-original_CenterOfMass  \
0  (114.35013341239252, 137.93240438778537, 127.3...   
1  (105.5636763627475, 144.51344414568564, 127.57...   
2  (128.06696716033483, 125.64842240824211, 125.5...   
3  (110.5198398681267, 125.62310137760508, 130.65...   
4  (112.50337605070966, 155.2838638555877, 129.34...   

   original_shape_Elongation  original_shape_Flatness  \
0                   0.407223                 0.096929   
1                   0.432795                 0.096712   
2                   0.422635                 0.107836   
3                   0.411789                 0.104226   
4                   0.437484                 0.099548   

   original_shape_LeastAxisLength  original_shape_MajorAxisLength  \
0                       10.641164                      109.782918   
1                       10.249435                      105.979255   
2                       11.116675                      103.088450   
3                       11.324564                      108.653645   
4                       10.281734                      103.283883   

   original_shape_Maximum2DDiameterColumn  \
0                               76.400262   
1                               77.103826   
2                               76.006579   
3                               81.024688   
4                               73.389373   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlice  \
0                            76.321688                              47.010637   
1                            78.025637                              47.169906   
2                            80.156098                              47.169906   
3                            82.024387                              49.091751   
4                            71.063352                              43.737855   

   original_shape_Maximum3DDiameter  original_shape_MeshVolume  \
0                         76.954532                6693.500000   
1                         78.051265                8113.875000   
2                         80.255841                7718.041667   
3                         85.539465                8392.250000   
4                         74.027022                7141.250000   

   original_shape_MinorAxisLength  original_shape_Sphericity  \
0                       44.706088                   0.382501   
1                       45.867286                   0.398037   
2                       43.568739                   0.387795   
3                       44.742336                   0.383549   
4                       45.185072                   0.397523   

   original_shape_SurfaceArea  original_shape_SurfaceVolumeRatio  \
0                 4490.419128              

**Handle remaining categorical features**

Since `diagnostics_Mask-original_BoundingBox` contains the bounding box coordinates of the region of interest, in this case the hippocampus, we can calculate the volume of this region to make the data more useful to our model, since a shrinkage of the hippocampus is linked to MCI (as stated in this project's assignment paper).

In [201]:
for value in df['diagnostics_Mask-original_BoundingBox']:
    coordinates = value.split(', ')
    x_max, y_max, z_max, x_min, y_min, z_min = [int(coordinate.replace("(", "").replace(")", "")) for coordinate in coordinates]
    if x_max <= x_min or y_max <= y_min or z_max <= z_min:
        print(coordinates)

['(89', '121', '86', '46', '31', '90)']


Bounding box coordinates are usually structured as such: `(x_min, y_min, z_min, x_max, y_max, z_max)`. However, by analyzing the data we can observe that the first 3 values are always bigger than the last 3 (except in two ocasions), so we can assume this data is actually being given to us as:  `(x_max, y_max, z_max, x_min, y_min, z_min)`.

In [202]:
volumes = []
i = 0

for value in df['diagnostics_Mask-original_BoundingBox']:
    coordinates = value.split(', ')
    x_max, y_max, z_max, x_min, y_min, z_min = [
        int(coordinate.replace("(", "").replace(")", "")) for coordinate in coordinates]
    # drop rows with invalid bounding box coordinates (max <= min)
    if x_max <= x_min or y_max <= y_min or z_max <= z_min:
        df.drop(i, axis=0, inplace=True)
    else:
        volumes.append((x_max - x_min) * (y_max - y_min) * (z_max - z_min))
    i += 1

df.drop(['diagnostics_Mask-original_BoundingBox'], axis=1, inplace=True)
df['BoundingBox_Volume'] = volumes
df['BoundingBox_Volume'].describe()

count        99.000000
mean      81950.656566
std       36689.781591
min        7616.000000
25%       58170.000000
50%       75803.000000
75%      108015.000000
max      167400.000000
Name: BoundingBox_Volume, dtype: float64

In [203]:
com_x = []
com_y = []
com_z = []

for value in df['diagnostics_Mask-original_CenterOfMassIndex']:
    coordinates = value.split(', ')
    x, y, z = [float(coordinate.replace("(", "").replace(")", "")) for coordinate in coordinates]
    com_x.append(x)
    com_y.append(y)
    com_z.append(z)

df.drop(['diagnostics_Mask-original_CenterOfMassIndex'], axis=1, inplace=True)
df.drop(['diagnostics_Mask-original_CenterOfMass'], axis=1, inplace=True)
df['CenterOfMass_X'] = com_x
df['CenterOfMass_Y'] = com_y
df['CenterOfMass_Z'] = com_z

df.head()

diagnostics_Image-original_Mean  diagnostics_Image-original_Maximum  \
0                         5.936274                                 138   
1                         6.727111                                 179   
2                         6.788788                                 161   
3                         6.925492                                 165   
4                         5.273378                                 176   

   diagnostics_Mask-original_VoxelNum  original_shape_Elongation  \
0                                6746                   0.407223   
1                                8182                   0.432795   
2                                7765                   0.422635   
3                                8493                   0.411789   
4                                7257                   0.437484   

   original_shape_Flatness  original_shape_LeastAxisLength  \
0                 0.096929                       10.641164   
1                 0.096712                       10.249435   
2                 0.107836                       11.116675   
3                 0.104226                       11.324564   
4                 0.099548                       10.281734   

   original_shape_MajorAxisLength  original_shape_Maximum2DDiameterColumn  \
0                      109.782918                               76.400262   
1                      105.979255                               77.103826   
2                      103.088450                               76.006579   
3                      108.653645                               81.024688   
4                      103.283883                               73.389373   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlice  \
0                            76.321688                              47.010637   
1                            78.025637                              47.169906   
2                            80.156098                              47.169906   
3                            82.024387                              49.091751   
4                            71.063352                              43.737855   

   original_shape_Maximum3DDiameter  original_shape_MeshVolume  \
0                         76.954532                6693.500000   
1                         78.051265                8113.875000   
2                         80.255841                7718.041667   
3                         85.539465                8392.250000   
4                         74.027022                7141.250000   

   original_shape_MinorAxisLength  original_shape_Sphericity  \
0                       44.706088                   0.382501   
1                       45.867286                   0.398037   
2                       43.568739                   0.387795   
3                       44.742336                   0.383549   
4                       45.185072                   0.397523   

   original_shape_SurfaceArea  original_shape_SurfaceVolumeRatio  \
0                 4490.419128                           0.670863   
1                 4905.837025                           0.604623   
2                 4870.279487                           0.631025   
3                 5206.936662                           0.620446   
4                 4511.332664                           0.631729   

   original_shape_VoxelVolume  original_firstorder_10Percentile  \
0                        6746                              54.0   
1                        8182                              55.0   
2                        7765                              53.0   
3                        8493                              59.0   
4                        7257                              60.0   

   original_firstorder_90Percentile  original_firstorder_Energy  \
0                                84                    33467265   
1                                83                    40602566   
2                              

In [187]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 303 entries, 0 to 304
Data columns (total 2018 columns):
 #     Column                                                         Non-Null Count  Dtype  
---    ------                                                         --------------  -----  
 0     diagnostics_Image-original_Mean                                303 non-null    float64
 1     diagnostics_Image-original_Maximum                             303 non-null    int64  
 2     diagnostics_Mask-original_VoxelNum                             303 non-null    int64  
 3     original_shape_Elongation                                      303 non-null    float64
 4     original_shape_Flatness                                        303 non-null    float64
 5     original_shape_LeastAxisLength                                 303 non-null    float64
 6     original_shape_MajorAxisLength                                 303 non-null    float64
 7     original_shape_Maximum2DDiameterColumn       

**Binary features?**

In [204]:
binary = [col for col, count in unique_dict.items() if count == 2]
for col in binary:
    print(col)
print("Total:", len(binary))

lbp-2D_firstorder_10Percentile
lbp-2D_firstorder_90Percentile
lbp-2D_firstorder_Median
lbp-3D-m1_firstorder_Median
Sex
Total: 5


### **Models**

Split data

In [189]:
X = df.drop('Transition', axis=1)
y = df['Transition']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=2024)

df.head()

diagnostics_Image-original_Mean  diagnostics_Image-original_Maximum  \
0                         5.848123                                 178   
1                         5.238834                                 190   
2                         6.816667                                 155   
3                         6.445162                                 171   
4                         5.568269                                 150   

   diagnostics_Mask-original_VoxelNum  original_shape_Elongation  \
0                                7106                   0.420040   
1                                7779                   0.425482   
2                                6707                   0.447685   
3                                8281                   0.418896   
4                                5986                   0.411851   

   original_shape_Flatness  original_shape_LeastAxisLength  \
0                 0.106547                       10.757474   
1                 0.102532                       10.432362   
2                 0.135582                       14.370911   
3                 0.099626                       10.639815   
4                 0.080719                        8.885188   

   original_shape_MajorAxisLength  original_shape_Maximum2DDiameterColumn  \
0                      100.964915                               72.034714   
1                      101.747321                               73.246160   
2                      105.993915                               79.762146   
3                      106.797600                               78.102497   
4                      110.075144                               75.432089   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlice  \
0                            71.175839                              43.416587   
1                            73.109507                              44.102154   
2                            79.056942                              47.853944   
3                            77.006493                              45.793013   
4                            75.239617                              43.462628   

   original_shape_Maximum3DDiameter  original_shape_MeshVolume  \
0                         72.034714                7033.166667   
1                         73.252986                7716.583333   
2                         81.154174                6636.083333   
3                         78.217645                8248.583333   
4                         75.848533                5897.791667   

   original_shape_MinorAxisLength  original_shape_Sphericity  \
0                       42.409319                   0.396075   
1                       43.291655                   0.420557   
2                       47.451935                   0.315524   
3                       44.737083                   0.401709   
4                       45.334518                   0.390626   

   original_shape_SurfaceArea  original_shape_SurfaceVolumeRatio  \
0                 4482.023762                           0.637270   
1                 4490.310227                           0.581904   
2                 5412.437400                           0.815607   
3                 4914.650931                           0.595818   
4                 4041.249915                           0.685214   

   original_shape_VoxelVolume  original_firstorder_10Percentile  \
0                        7106                              56.0   
1                        7779                              56.0   
2                        6707                              34.0   
3                        8281                              59.0   
4                        5986                              60.0   

   original_firstorder_90Percentile  original_firstorder_Energy  \
0                              83.0                    35914043   
1                              82.0                    38292768   
2                              

#### Decision Tree

In [190]:
dt_model = DecisionTreeClassifier(max_depth=2, random_state=2024)
dt_model.fit(X_train, y_train)

DecisionTreeClassifier(max_depth=2, random_state=2024)

In [191]:
dt_score = dt_model.score(X_test, y_test)
print("Accuracy: %.2f%%" % (dt_score * 100))

Accuracy: 44.26%
